In [1]:
#https://towardsdatascience.com/reinforcement-learning-implement-tictactoe-189582bea542

import numpy as np
import pickle

BOARD_ROWS = 3
BOARD_COLS = 3

In [3]:
"""Reinforcement learning is particularly opportune for such comparisons. At its core, any reinforcement 
learning task is defined by three things — states, actions and rewards. States are a representation of the 
current world or environment of the task. Actions are something an RL agent can do to change these states. 
And rewards are the utility the agent receives for performing the “right” actions. So the states tell the 
agent what situation it is in currently, and the rewards signal the states that it should be aspiring towards. """
class Agent2:
    def __init__(self,symbol):
        self.states=[]
        self.states_value = {}
        self.lr = 0.2
        self.exp_rate = 0.1
        self.decay_gamma = 0.9
        self.symbol=symbol
        
        
    def addState(self, state):
        self.states.append(state)

    # at the end of game, backpropagate and update states value
    def feedReward(self, reward):
        for state in reversed(self.states):
            if self.states_value.get(state) is None:
                self.states_value[state] = 0
            self.states_value[state] += self.lr * (self.decay_gamma * reward - self.states_value[state])
            #print(self.states_value[state])
            reward = self.states_value[state]

    def reset(self):
        self.states = []        

    def chooseAction(self, positions, current_board):
        if np.random.uniform(0, 1) <= self.exp_rate:
            # take random action
            idx = np.random.choice(len(positions))
            action = positions[idx]
        else:   
            value_max = -999
            for p in positions:
                next_board = current_board.copy()
                next_board[p] = self.symbol
                next_boardHash = self.getHash(next_board)
                value = 0 if self.states_value.get(next_boardHash) is None else self.states_value.get(next_boardHash)
                #print(self.states_value.get(next_boardHash))
                if value >= value_max:
                    value_max = value
                    action = p
        return action
    def getHash(self,board):
        boardHash = str(board.reshape(BOARD_COLS * BOARD_ROWS))
        return boardHash

class State2:
    def __init__(self):
        self.board = np.zeros((BOARD_ROWS, BOARD_COLS))
        self.boardHash = None

    def getCurrentBoardHash(self):
        boardHash = str(self.board.reshape(BOARD_COLS * BOARD_ROWS))
        return boardHash

    def reset(self):
        self.board = np.zeros((BOARD_ROWS, BOARD_COLS))
        self.boardHash = None
        
    def showBoard(self):
        # p1: x  p2: o
        for i in range(0, BOARD_ROWS):
            print('-------------')
            out = '| '
            for j in range(0, BOARD_COLS):
                if self.board[i, j] == 1:
                    token = 'x'
                if self.board[i, j] == -1:
                    token = 'o'
                if self.board[i, j] == 0:
                    token = ' '
                out += token + ' | '
            print(out)
        print('-------------')      
    def updateBoardState(self, position,playerSymbol):
        self.board[position] = playerSymbol
        # switch to another player
        #self.playerSymbol = -1 if self.playerSymbol == 1 else 1
    def availablePositions(self):
        positions = []
        for i in range(BOARD_ROWS):
            for j in range(BOARD_COLS):
                if self.board[i, j] == 0:
                    positions.append((i, j))  # need to be tuple
        return positions        
    def winner(self):
        # row
        for i in range(BOARD_ROWS):
            if sum(self.board[i, :]) == 3:
                self.isEnd = True
                return 1
            if sum(self.board[i, :]) == -3:
                self.isEnd = True
                return -1
        # col
        for i in range(BOARD_COLS):
            if sum(self.board[:, i]) == 3:
                self.isEnd = True
                return 1
            if sum(self.board[:, i]) == -3:
                self.isEnd = True
                return -1
        # diagonal
        diag_sum1 = sum([self.board[i, i] for i in range(BOARD_COLS)])
        diag_sum2 = sum([self.board[i, BOARD_COLS - i - 1] for i in range(BOARD_COLS)])
        diag_sum = max(abs(diag_sum1), abs(diag_sum2))
        if diag_sum == 3:
            self.isEnd = True
            if diag_sum1 == 3 or diag_sum2 == 3:
                return 1
            else:
                return -1

        # tie
        # no available positions
        if len(self.availablePositions()) == 0:
            self.isEnd = True
            return 0
        # not end
        self.isEnd = False
        return None        
    def giveReward(self,result):
        reward1=0
        reward2=0
        # backpropagate reward
        if result == 1:
            reward1=1
            reward2=0
        elif result == -1:
            reward1=0
            reward2=1
        else:
            reward1=.1
            reward2=.5
  
        return(reward1,reward2)
    
st = State2()
agent1=Agent2(-1)
agent2=Agent2(1)

def checkForWinner(st,agent1,agent2):
    win = st.winner()
    retVal="";
    if win is not None:
        #print(win)
        reward1,reward2=st.giveReward(win)
        agent1.feedReward(reward1)
        agent2.feedReward(reward2)
        if win is not None:
            if win == -1:
                retVal="p2 wins!"
            elif win==1:
                retVal="p1 wins!"
            elif win==0:
                retVal="Draw"
        st.showBoard()
        st.reset()
        agent1.reset()
        agent2.reset()
    return retVal
    

for i in np.arange(0,1000):
    #st.updateBoardState((2,1),1)
    #st.updateBoardState((2,0),1)
    #t.updateBoardState((2,2),1)
    #st.updateBoardState((1,1),-1)
    #st.updateBoardState((1,0),-1)
    #st.updateBoardState((1,2),-1)

    #tprint(st.getCurrentBoardHash())
    winner=checkForWinner(st,agent1,agent2)
    if winner=="":
        positions=st.availablePositions()
        action=agent1.chooseAction(positions,st.board)
        #print(action)
        st.updateBoardState(action,-1)    
        agent1.addState(st.getCurrentBoardHash())
    else:
        print(winner)
        
    winner=checkForWinner(st,agent1,agent2)
    if winner=="":
        positions=st.availablePositions()
        action=agent2.chooseAction(positions,st.board)
        #print(action)
        st.updateBoardState(action,1)    
        agent2.addState(st.getCurrentBoardHash())
        
        print(len(agent2.states_value))

        for state,value in agent2.states_value.items():
            print(state,value)

    else:
        print(winner)
        
        



0
0
0
-------------
|   |   | o | 
-------------
| x | o | x | 
-------------
| o | x | o | 
-------------
p2 wins!
3
[ 0.  0.  0.  1. -1.  1. -1.  1. -1.] 0.18000000000000002
[ 0.  0.  0.  0.  0.  1. -1.  1. -1.] 0.032400000000000005
[ 0.  0.  0.  0.  0.  0.  0.  1. -1.] 0.005832000000000001
3
[ 0.  0.  0.  1. -1.  1. -1.  1. -1.] 0.18000000000000002
[ 0.  0.  0.  0.  0.  1. -1.  1. -1.] 0.032400000000000005
[ 0.  0.  0.  0.  0.  0.  0.  1. -1.] 0.005832000000000001
3
[ 0.  0.  0.  1. -1.  1. -1.  1. -1.] 0.18000000000000002
[ 0.  0.  0.  0.  0.  1. -1.  1. -1.] 0.032400000000000005
[ 0.  0.  0.  0.  0.  0.  0.  1. -1.] 0.005832000000000001
3
[ 0.  0.  0.  1. -1.  1. -1.  1. -1.] 0.18000000000000002
[ 0.  0.  0.  0.  0.  1. -1.  1. -1.] 0.032400000000000005
[ 0.  0.  0.  0.  0.  0.  0.  1. -1.] 0.005832000000000001
-------------
| o | x | x | 
-------------
| o | o | x | 
-------------
| o | x | o | 
-------------
p2 wins!
5
[ 0.  0.  0.  1. -1.  1. -1.  1. -1.] 0.18000000000000002
[ 

[ 1.  0.  0.  0.  0.  0.  0.  0. -1.] 0.0010497600000000003
[ 0. -1.  1. -1.  1. -1.  1. -1.  1.] 0.0
[ 0. -1.  0.  0.  1. -1.  1. -1.  1.] 0.0
[ 0. -1.  0.  0.  0.  0.  1. -1.  1.] 0.0
[ 0.  0.  0.  0.  0.  0.  0. -1.  1.] 0.0
[ 0.  0.  1. -1.  1. -1.  1. -1.  1.] 0.0
[ 0.  0.  0.  0.  1. -1.  1. -1.  1.] 0.0
[ 0.  0.  0.  0.  0.  0.  1. -1.  1.] 0.0
[0. 0. 0. 0. 0. 0. 0. 0. 1.] 0.0010497600000000003
[ 1.  0.  0.  1. -1.  1. -1. -1.  1.] 0.18000000000000002
[ 1.  0.  0.  0.  0.  1. -1. -1.  1.] 0.032400000000000005
[ 1.  0.  0.  0.  0.  0.  0. -1.  1.] 0.005832000000000001
-------------
|   | o | x | 
-------------
| o | x | o | 
-------------
| x | o | x | 
-------------
p1 wins!
20
[ 0.  0.  0.  1. -1.  1. -1.  1. -1.] 0.6050880000000001
[ 0.  0.  0.  0.  0.  1. -1.  1. -1.] 0.2788929792
[ 0.  0.  0.  0.  0.  0.  0.  1. -1.] 0.10958747904
[ 0.  1.  1. -1. -1.  1. -1.  1. -1.] 0.18000000000000002
[ 0.  0.  1.  0. -1.  1. -1.  1. -1.] 0.032400000000000005
[ 1.  0.  1. -1. -1.  1.  1. 

25
[ 0.  0.  0.  1. -1.  1. -1.  1. -1.] 0.6050880000000001
[ 0.  0.  0.  0.  0.  1. -1.  1. -1.] 0.2788929792
[ 0.  0.  0.  0.  0.  0.  0.  1. -1.] 0.10958747904
[ 0.  1.  1. -1. -1.  1. -1.  1. -1.] 0.18000000000000002
[ 0.  0.  1.  0. -1.  1. -1.  1. -1.] 0.032400000000000005
[ 1.  0.  1. -1. -1.  1.  1. -1. -1.] 0.18000000000000002
[ 1.  0.  0.  0. -1.  1.  1. -1. -1.] 0.032400000000000005
[ 1.  0.  0.  0.  0.  0.  1. -1. -1.] 0.005832000000000001
[ 1.  0.  0.  0.  0.  0.  0.  0. -1.] 0.0010497600000000003
[ 0. -1.  1. -1.  1. -1.  1. -1.  1.] 0.0
[ 0. -1.  0.  0.  1. -1.  1. -1.  1.] 0.0
[ 0. -1.  0.  0.  0.  0.  1. -1.  1.] 0.0
[ 0.  0.  0.  0.  0.  0.  0. -1.  1.] 0.0
[ 0.  0.  1. -1.  1. -1.  1. -1.  1.] 0.0
[ 0.  0.  0.  0.  1. -1.  1. -1.  1.] 0.0
[ 0.  0.  0.  0.  0.  0.  1. -1.  1.] 0.0
[0. 0. 0. 0. 0. 0. 0. 0. 1.] 0.01611631862784
[ 1.  0.  0.  1. -1.  1. -1. -1.  1.] 0.324
[ 1.  0.  0.  0.  0.  1. -1. -1.  1.] 0.034504704000000004
[ 1.  0.  0.  0.  0.  0.  0. -1.  1.] 0.0

[ 0.  0.  0.  0.  0.  1. -1.  1. -1.] 0.2788929792
[ 0.  0.  0.  0.  0.  0.  0.  1. -1.] 0.10958747904
[ 0.  1.  1. -1. -1.  1. -1.  1. -1.] 0.18000000000000002
[ 0.  0.  1.  0. -1.  1. -1.  1. -1.] 0.032400000000000005
[ 1.  0.  1. -1. -1.  1.  1. -1. -1.] 0.18000000000000002
[ 1.  0.  0.  0. -1.  1.  1. -1. -1.] 0.032400000000000005
[ 1.  0.  0.  0.  0.  0.  1. -1. -1.] 0.005832000000000001
[ 1.  0.  0.  0.  0.  0.  0.  0. -1.] 0.0010497600000000003
[ 0. -1.  1. -1.  1. -1.  1. -1.  1.] 0.0
[ 0. -1.  0.  0.  1. -1.  1. -1.  1.] 0.025920000000000006
[ 0. -1.  0.  0.  0.  0.  1. -1.  1.] 0.009331200000000001
[ 0.  0.  0.  0.  0.  0.  0. -1.  1.] 0.002519424000000001
[ 0.  0.  1. -1.  1. -1.  1. -1.  1.] 0.0
[ 0.  0.  0.  0.  1. -1.  1. -1.  1.] 0.0
[ 0.  0.  0.  0.  0.  0.  1. -1.  1.] 0.0
[0. 0. 0. 0. 0. 0. 0. 0. 1.] 0.02694753551351808
[ 1.  0.  0.  1. -1.  1. -1. -1.  1.] 0.43920000000000003
[ 1.  0.  0.  0.  0.  1. -1. -1.  1.] 0.08091120844800001
[ 1.  0.  0.  0.  0.  0.  0. -1.  

[ 0. -1.  1. -1.  1. -1.  1. -1.  1.] 0.0
[ 0. -1.  0.  0.  1. -1.  1. -1.  1.] 0.025920000000000006
[ 0. -1.  0.  0.  0.  0.  1. -1.  1.] 0.009331200000000001
[ 0.  0.  0.  0.  0.  0.  0. -1.  1.] 0.002519424000000001
[ 0.  0.  1. -1.  1. -1.  1. -1.  1.] 0.0
[ 0.  0.  0.  0.  1. -1.  1. -1.  1.] 0.0
[ 0.  0.  0.  0.  0.  0.  1. -1.  1.] 0.0
[0. 0. 0. 0. 0. 0. 0. 0. 1.] 0.03277918641893149
[ 1.  0.  0.  1. -1.  1. -1. -1.  1.] 0.43920000000000003
[ 1.  0.  0.  0.  0.  1. -1. -1.  1.] 0.026512984784240645
[ 1.  0.  0.  0.  0.  0.  0. -1.  1.] 0.039979021436662585
[ 1. -1. -1.  0.  1. -1.  1. -1.  1.] 0.0
[ 1.  0. -1.  0.  1.  1. -1. -1.  1.] 0.0
[ 0. -1.  0.  1. -1.  1. -1.  1.  1.] 0.18000000000000002
[ 0. -1.  0.  0.  0.  1. -1.  1.  1.] 0.032400000000000005
[ 0. -1.  0.  0.  0.  0.  0.  1.  1.] 0.005832000000000001
[ 0. -1. -1.  1.  1. -1.  1. -1.  1.] 0.18000000000000002
[ 0.  0.  1.  0.  0.  1. -1. -1.  1.] 0.0
[ 0.  0.  1.  0.  0.  0.  0. -1.  1.] 0.0
[ 0.  0.  1.  0.  0.  0. -1.

...

[ 0.  1. -1.  1. -1. -1.  1. -1.  1.] 0.09000000000000001
[ 0.  0.  0.  1. -1. -1.  1. -1.  1.] 0.012960000000000003
[ 0.  0.  0.  0. -1.  0.  1. -1.  1.] 0.004665600000000001
[ 0.  0.  0.  0. -1.  0.  0.  0.  1.] 0.0005248800000000001
[ 1. -1.  1.  1.  1. -1. -1. -1.  1.] 0.0
[ 0.  0.  1.  1.  1. -1. -1. -1.  1.] 0.0
[ 0.  0.  1.  0.  1.  0. -1. -1.  1.] 0.0
[ 0. -1. -1.  0.  0.  1.  1. -1.  1.] 0.18000000000000002
[-1.  0.  1. -1.  1. -1.  1. -1.  1.] 0.0
[-1.  0.  0.  0.  1. -1.  1. -1.  1.] 0.0
[-1.  0.  0.  0.  0.  0.  1. -1.  1.] 0.019110297600000003
[-1.  0.  0.  0.  0.  0.  0.  0.  1.] 0.010497600000000003
[0. 0. 0. 0. 0. 0. 0. 1. 0.] 0.0035691840000000013
[ 1.  0. -1.  1.  0.  1. -1. -1.  1.] 0.18000000000000002
[ 0. -1. -1.  0.  0.  1. -1.  1.  1.] 0.18000000000000002
[ 0. -1. -1.  0.  0.  0.  0.  1.  1.] 0.032400000000000005
[ 0. -1.  0.  0.  0.  0.  0.  0.  1.] 0.49860998077816393
[ 1. -1.  0.  0.  1. -1.  1. -1.  1.] 0.0
[ 1. -1.  0.  0.  0.  0.  1. -1.  1.] 0.0
[ 0.  0.  

[ 0.  0.  1.  0.  0.  1. -1. -1.  1.] 0.0
[ 0.  0.  1.  0.  0.  0.  0. -1.  1.] 0.0
[ 0.  0.  1.  0.  0.  0. -1.  0.  1.] 0.0
[0. 0. 1. 0. 0. 0. 0. 0. 0.] 0.0
[ 1.  1. -1.  0.  0.  1. -1. -1.  1.] 0.6705219767500801
[ 0.  0.  0.  1.  0.  1. -1. -1.  1.] 0.379020321792
[ 0.  0.  0.  1.  0.  0.  0. -1.  1.] 0.017216064000000003
[ 0.  0. -1.  0.  1. -1.  1. -1.  1.] 0.1962144
[ 0.  0. -1.  0.  0.  0.  1. -1.  1.] 0.06013958400000001
[ 0.  1. -1.  1. -1. -1.  1. -1.  1.] 0.09000000000000001
[ 0.  0.  0.  1. -1. -1.  1. -1.  1.] 0.012960000000000003
[ 0.  0.  0.  0. -1.  0.  1. -1.  1.] 0.004665600000000001
[ 0.  0.  0.  0. -1.  0.  0.  0.  1.] 0.0005248800000000001
[ 1. -1.  1.  1.  1. -1. -1. -1.  1.] 0.0
[ 0.  0.  1.  1.  1. -1. -1. -1.  1.] 0.0
[ 0.  0.  1.  0.  1.  0. -1. -1.  1.] 0.0
[ 0. -1. -1.  0.  0.  1.  1. -1.  1.] 0.18000000000000002
[-1.  0.  1. -1.  1. -1.  1. -1.  1.] 0.0
[-1.  0.  0.  0.  1. -1.  1. -1.  1.] 0.0
[-1.  0.  0.  0.  0.  0.  1. -1.  1.] 0.019110297600000003
[-1

152
[ 0.  0.  0.  1. -1.  1. -1.  1. -1.] 0.6050880000000001
[ 0.  0.  0.  0.  0.  1. -1.  1. -1.] 0.2788929792
[ 0.  0.  0.  0.  0.  0.  0.  1. -1.] 0.10958747904
[ 0.  1.  1. -1. -1.  1. -1.  1. -1.] 0.18000000000000002
[ 0.  0.  1.  0. -1.  1. -1.  1. -1.] 0.032400000000000005
[ 1.  0.  1. -1. -1.  1.  1. -1. -1.] 0.324
[ 1.  0.  0.  0. -1.  1.  1. -1. -1.] 0.08424000000000001
[ 1.  0.  0.  0.  0.  0.  1. -1. -1.] 0.019828800000000004
[ 1.  0.  0.  0.  0.  0.  0.  0. -1.] 0.0010497600000000003
[ 0. -1.  1. -1.  1. -1.  1. -1.  1.] 0.0
[ 0. -1.  0.  0.  1. -1.  1. -1.  1.] 0.002783138807808001
[ 0. -1.  0.  0.  0.  0.  1. -1.  1.] 0.607908233185864
[ 0.  0.  0.  0.  0.  0.  0. -1.  1.] 0.28961334199509287
[ 0.  0.  1. -1.  1. -1.  1. -1.  1.] 0.0
[ 0.  0.  0.  0.  1. -1.  1. -1.  1.] 0.0
[ 0.  0.  0.  0.  0.  0.  1. -1.  1.] 0.0
[0. 0. 0. 0. 0. 0. 0. 0. 1.] 0.05997065114096878
[ 1.  0.  0.  1. -1.  1. -1. -1.  1.] 0.7792040448
[ 1.  0.  0.  0.  0.  1. -1. -1.  1.] 0.00601872479755189

[ 1. -1.  0.  0.  1. -1.  1. -1.  1.] 0.0
[ 1. -1.  0.  0.  0.  0.  1. -1.  1.] 0.0
[ 0.  0.  1. -1. -1.  1. -1.  1.  1.] 0.0
[ 0.  0.  0. -1.  0.  1. -1.  1.  1.] 0.0
[ 0.  0.  0. -1.  0.  0.  0.  1.  1.] 0.0
[ 1. -1.  0.  0.  0. -1.  1. -1.  1.] 0.18000000000000002
[ 0. -1.  0.  1.  0. -1.  1. -1.  1.] 0.8916989651668307
[-1. -1.  0.  0.  0.  1.  1. -1.  1.] 0.43920000000000003
[ 1. -1.  0. -1.  1. -1.  1. -1.  1.] 0.0
[ 1. -1.  0. -1.  0.  0.  1. -1.  1.] 0.0
[ 1. -1.  0.  1.  0. -1.  1. -1.  1.] 0.0
[ 0.  0.  1.  0.  1. -1.  1. -1. -1.] 0.0
[ 0.  0.  1.  0.  0.  0.  1. -1. -1.] 0.0
[ 0.  0.  1.  0.  0.  0.  0. -1.  0.] 0.0
[ 0.  1. -1.  1.  1. -1. -1. -1.  1.] 0.162
[ 0.  0.  0.  1.  1. -1. -1. -1.  1.] 0.156231535104
[ 0.  0.  0.  1.  0. -1.  0. -1.  1.] 0.07920685207756802
[ 0. -1.  0.  1.  0.  0.  0. -1.  1.] 0.17640000000000003
[ 0. -1.  1.  0.  0. -1.  1. -1.  1.] 0.18000000000000002
[ 1. -1.  0.  0.  0.  1. -1. -1.  1.] 0.324
[ 1. -1.  0.  0.  0.  0.  0. -1.  1.] 0.0324000000

[ 0.  0.  0.  0.  0.  0.  0. -1.  1.] 0.28973800556850526
[ 0.  0.  1. -1.  1. -1.  1. -1.  1.] 0.0
[ 0.  0.  0.  0.  1. -1.  1. -1.  1.] 0.0
[ 0.  0.  0.  0.  0.  0.  1. -1.  1.] 0.0
[0. 0. 0. 0. 0. 0. 0. 0. 1.] 0.05997065114096878
[ 1.  0.  0.  1. -1.  1. -1. -1.  1.] 0.7792040448
[ 1.  0.  0.  0.  0.  1. -1. -1.  1.] 0.006018724797551897
[ 1.  0.  0.  0.  0.  0.  0. -1.  1.] 0.016430695364901583
[ 1. -1. -1.  0.  1. -1.  1. -1.  1.] 0.0
[ 1.  0. -1.  0.  1.  1. -1. -1.  1.] 0.0
[ 0. -1.  0.  1. -1.  1. -1.  1.  1.] 0.324
[ 0. -1.  0.  0.  0.  1. -1.  1.  1.] 0.08424000000000001
[ 0. -1.  0.  0.  0.  0.  0.  1.  1.] 0.019828800000000004
[ 0. -1. -1.  1.  1. -1.  1. -1.  1.] 0.53136
[ 0.  0.  1.  0.  0.  1. -1. -1.  1.] 0.0
[ 0.  0.  1.  0.  0.  0.  0. -1.  1.] 0.0
[ 0.  0.  1.  0.  0.  0. -1.  0.  1.] 0.0
[0. 0. 1. 0. 0. 0. 0. 0. 0.] 0.0
[ 1.  1. -1.  0.  0.  1. -1. -1.  1.] 0.6705219767500801
[ 0.  0.  0.  1.  0.  1. -1. -1.  1.] 0.379020321792
[ 0.  0.  0.  1.  0.  0.  0. -1.  1.] 